# Competition Recommender Systems

In [1]:
from google.colab import drive
drive.mount('/content/drive', True)

Mounted at /content/drive


In [2]:
import sys
sys.path.insert(0,'/content/drive/MyDrive/Competition_Recommender_Systems')

In [3]:
import os
from typing import Tuple, Callable, Dict, Optional, List

import numpy as np
import pandas as pd
import scipy.sparse as sp

from sklearn.model_selection import train_test_split

cwd = '/content/drive/MyDrive/Competition_Recommender_Systems'

## Data Manipulation

In [4]:
!pip install implicit

In [5]:
def load_data(file_path, load_users=False):
    data = pd.read_csv(file_path)
    
    if load_users:
        user_list = data['user_id'].tolist()
        return user_list
    else:
        user_list = data['row'].tolist()
        item_list = data['col'].tolist()
        rating_list = data['data'].tolist()
        return sp.coo_matrix((rating_list, (user_list, item_list))).tocsr()

In [6]:
ratings = load_data(os.path.join(cwd, 'dataset', 'data_train.csv'))

icm_all = load_data(os.path.join(cwd, 'dataset', 'data_ICM_title_abstract.csv'))

target_users = load_data(os.path.join(cwd, 'dataset', 'data_target_users_test.csv'), load_users=True)

for i in range(7947):
    if i not in target_users:
        print("Missing user: {}".format(i))

Missing user: 1304
Missing user: 2245
Missing user: 4319


## Bayesian search

### Cross Validation

In [7]:
from CrossValidation.CrossValidation import CrossKValidator_With_URM_stack
from KNN.ItemKNNCBFRecommender import ItemKNNCBFRecommender
from KNN.ItemKNNCFRecommender import ItemKNNCFRecommender
from MatrixFactorization.IALSRecommender_implicit import IALSRecommender
from GraphBased.RP3betaRecommender import RP3betaRecommender

from bayes_opt import BayesianOptimization
import pandas as pd
import csv
import numpy as np

k = 5
cross_validator = CrossKValidator_With_URM_stack(URM_all=ratings, ICM_all=icm_all, k=k)
evaluator_list, URM_train_list, URM_validation_list, URM_stack_list = cross_validator.creating_k_evaluator_with_URM_stack_ICM()

### Tuning RP3beta

In [17]:
tuning_params = {
    "topK": (0, 3000),
    "alpha": (0, 1),
    "beta": (0, 1)
}


def BO_func(topK, alpha, beta):
    cumulative_MAP = 0

    for i in range(k):
        RP3beta = RP3betaRecommender(URM_stack_list[i])
        RP3beta.fit(topK=int(topK), alpha=alpha, beta=beta, implicit=True, normalize_similarity=False)
        MAP = evaluator_list[i].evaluateRecommender(RP3beta)[0][5]["MAP"]
        cumulative_MAP += MAP

    return cumulative_MAP/k

In [18]:
optimizer = BayesianOptimization(
    f=BO_func,
    pbounds=tuning_params,
    verbose=5,
    random_state=30
)

optimizer.maximize(
    init_points=30,
    n_iter=70
)

|   iter    |  target   |   alpha   |   beta    |   topK    |
-------------------------------------------------------------
RP3betaRecommender: URM Detected 83 (0.30 %) cold users.
RP3betaRecommender: URM Detected 1 (0.00 %) cold items.
EvaluatorHoldout: Processed 5605 ( 100.00% ) in 4.93 sec. Users per second: 1137
RP3betaRecommender: URM Detected 69 (0.25 %) cold users.
RP3betaRecommender: URM Detected 3 (0.01 %) cold items.
EvaluatorHoldout: Processed 5673 ( 100.00% ) in 4.97 sec. Users per second: 1141
RP3betaRecommender: URM Detected 75 (0.27 %) cold users.
RP3betaRecommender: URM Detected 1 (0.00 %) cold items.
EvaluatorHoldout: Processed 5689 ( 100.00% ) in 5.02 sec. Users per second: 1133
RP3betaRecommender: URM Detected 67 (0.24 %) cold users.
RP3betaRecommender: URM Detected 3 (0.01 %) cold items.
EvaluatorHoldout: Processed 5624 ( 100.00% ) in 4.90 sec. Users per second: 1147
RP3betaRecommender: URM Detected 68 (0.24 %) cold users.
RP3betaRecommender: URM Detected 1 (0.00 %)

In [19]:
optimizer.max

{'params': {'alpha': 0.38770822445994335,
  'beta': 0.3570967475164035,
  'topK': 2959.152428955479},
 'target': 0.06882828731040763}

### Tuning iALS

In [21]:
import implicit

tuning_params = {
    "num_factors": (400, 700),
    "reg": (1e-9, 1e-1),
    "iterations": (200, 400),
    "alpha": (1, 50),
    "epsilon": (1e-9, 1e-2),
    "confidence_scaling": (0, 1)
}


def BO_func(num_factors, reg, iterations, alpha, epsilon, confidence_scaling):
    cumulative_MAP = 0

    for i in range(k):
      iALS = IALSRecommender(URM_stack_list[i])
      if round(confidence_scaling):
        conf_scal = "log"  
      else:
        conf_scal = "linear"
      iALS.fit(n_factors=int(num_factors), reg=reg, iterations=int(iterations), confidence_scaling=conf_scal, alpha=alpha, epsilon=epsilon, use_gpu=True)
      MAP = evaluator_list[i].evaluateRecommender(iALS)[0][5]["MAP"]
      cumulative_MAP += MAP

    return cumulative_MAP/k

In [22]:
optimizer = BayesianOptimization(
    f=BO_func,
    pbounds=tuning_params,
    verbose=5,
    random_state=30
)

optimizer.maximize(
    init_points=30,
    n_iter=70
)

|   iter    |  target   |   alpha   | confid... |  epsilon  | iterat... | num_fa... |    reg    |
-------------------------------------------------------------------------------------------------
IALSRecommender: URM Detected 66 (0.24 %) cold users.
IALSRecommender: URM Detected 1 (0.00 %) cold items.



EvaluatorHoldout: Processed 5647 ( 100.00% ) in 6.71 sec. Users per second: 842


IALSRecommender: URM Detected 55 (0.20 %) cold users.
IALSRecommender: URM Detected 2 (0.01 %) cold items.



EvaluatorHoldout: Processed 5660 ( 100.00% ) in 6.46 sec. Users per second: 876


IALSRecommender: URM Detected 76 (0.27 %) cold users.
IALSRecommender: URM Detected 1 (0.00 %) cold items.


...


EvaluatorHoldout: Processed 5649 ( 100.00% ) in 5.81 sec. Users per second: 973


IALSRecommender: URM Detected 75 (0.27 %) cold users.



EvaluatorHoldout: Processed 5653 ( 100.00% ) in 5.87 sec. Users per second: 963


IALSRecommender: URM Detected 76 (0.27 %) cold users.
IALSRecommender: URM Detected 3 (0.01 %) cold items.



EvaluatorHoldout: Processed 5635 ( 100.00% ) in 6.06 sec. Users per second: 930
|  100      |  0.07308  |  28.27    |  0.2185   |  0.006442 |  399.4    |  510.2    |  0.04732  |


In [23]:
optimizer.max

{'params': {'alpha': 28.297488854932897,
  'confidence_scaling': 0.05308799484791482,
  'epsilon': 0.003603663994262537,
  'iterations': 200.93031138839658,
  'num_factors': 622.2250097807862,
  'reg': 0.030756138926585266},
 'target': 0.07417865390994278}

In [15]:
import implicit

tuning_params = {
    "num_factors": (400, 600),
    "reg": (1e-10, 1e-8),
    "iterations": (1, 50),
    "alpha": (30, 60)
}


def BO_func(num_factors, reg, iterations, alpha):
    cumulative_MAP = 0

    for i in range(k):
      iALS = IALSRecommender(URM_stack_list[i])
      iALS.fit(n_factors=int(num_factors), reg=reg, iterations=int(iterations), confidence_scaling="linear", alpha=alpha, use_gpu=True)
      MAP = evaluator_list[i].evaluateRecommender(iALS)[0][5]["MAP"]
      cumulative_MAP += MAP

    return cumulative_MAP/k

In [16]:
optimizer = BayesianOptimization(
    f=BO_func,
    pbounds=tuning_params,
    verbose=5,
    random_state=30
)

optimizer.maximize(
    init_points=30,
    n_iter=70
)

|   iter    |  target   |   alpha   | iterat... | num_fa... |    reg    |
-------------------------------------------------------------------------
IALSRecommender: URM Detected 66 (0.24 %) cold users.
IALSRecommender: URM Detected 1 (0.00 %) cold items.



EvaluatorHoldout: Processed 5647 ( 100.00% ) in 5.87 sec. Users per second: 961


IALSRecommender: URM Detected 55 (0.20 %) cold users.
IALSRecommender: URM Detected 2 (0.01 %) cold items.



EvaluatorHoldout: Processed 5660 ( 100.00% ) in 5.66 sec. Users per second: 999


IALSRecommender: URM Detected 76 (0.27 %) cold users.
IALSRecommender: URM Detected 1 (0.00 %) cold items.


...


EvaluatorHoldout: Processed 5649 ( 100.00% ) in 6.14 sec. Users per second: 920


IALSRecommender: URM Detected 75 (0.27 %) cold users.



EvaluatorHoldout: Processed 5653 ( 100.00% ) in 6.23 sec. Users per second: 908


IALSRecommender: URM Detected 76 (0.27 %) cold users.
IALSRecommender: URM Detected 3 (0.01 %) cold items.



EvaluatorHoldout: Processed 5635 ( 100.00% ) in 6.02 sec. Users per second: 936
|  100      |  0.07301  |  48.96    |  28.04    |  599.7    |  7.508e-0 |


In [20]:
optimizer.max

{'params': {'alpha': 32.563033267348416,
  'confidence_scaling': 0.38074848963511654,
  'epsilon': 0.006630479390308782,
  'iterations': 232.73014522055067,
  'num_factors': 688.7823441022956,
  'reg': 0.03466618469131473},
 'target': 0.07361255183816187}